In [1]:
import numpy as np
import joblib as jl
import pandas as pd

from rdkit import Chem
from rdkit.Chem import AllChem
from rdkit.Chem import Draw

**1. Small molecule screening**


In [2]:
from src.moleculescreen import getrncaa

In [3]:
getrncaa('./molslibrary/L-alanine.sdf','./molslibrary/L-alamatch.csv')
getrncaa('./molslibrary/L-phenylalanine.sdf','./molslibrary/L-phematch.csv')
getrncaa('./molslibrary/L-tryptophan.sdf','./molslibrary/L-trpmatch.csv')
getrncaa('./molslibrary/L-tyrosine.sdf','./molslibrary/L-tyrmatch.csv')

The name of file: L-alanine.sdf


[21:39:58] WARNING: not removing hydrogen atom without neighbors
[21:40:05] WARNING: not removing hydrogen atom without neighbors


The number of molecules: 18697
matching: 950
not_matching: 17747
Second clean-up: 713
Third clean-up: 710


The name of file: L-phenylalanine.sdf
The number of molecules: 7753
matching: 557
not_matching: 7196
Second clean-up: 411
Third clean-up: 406


The name of file: L-tryptophan.sdf
The number of molecules: 1932
matching: 225
not_matching: 1707
Second clean-up: 171
Third clean-up: 171


The name of file: L-tyrosine.sdf
The number of molecules: 3718
matching: 431
not_matching: 3287
Second clean-up: 277
Third clean-up: 276




In [4]:
#Merge molecular libraries and de-duplicate
df = pd.DataFrame(columns=['SMILES','Name'])
smis= []
lenth = []
for file in ['L-phematch.csv','L-tyrmatch.csv','L-trpmatch.csv','L-alamatch.csv']:
        df1 = pd.read_csv('./molslibrary/'+file)
        df1['Name']=file[2:5]
        df = pd.concat([df,df1],axis=0)

df =df[~df['SMILES'].duplicated (keep='first')] 
df.reset_index(drop=True,inplace=True)
print(df['Name'].value_counts())
df.to_csv('./molslibrary/allsmi.csv',index=False)

ala    644
phe    406
tyr    253
trp    171
Name: Name, dtype: int64


**2. Get the Chemopy descriptors**


- After obtaining the smiles format of the screened molecules, obtain the chemopy descriptors from ChemDes (http://www.scbdd.com/chemopy_desc/index/) or PyBioMed (https://github.com/gadsbyfly/PyBioMed). The ChemDes platform only supports the calculation of 500 small molecules at a time, while PyBioMed can be downloaded locally to calculate large batches of small molecules.



- If you expect to calculate Chemopy descriptors by PyBioMed, you can create a conda envrioment by the file 'pybiomed.yaml'.The follow command can help:\
   ``` conda env create -f pybiomed.yaml```


- Here you need to change the conda environment to 'pybiomed', then run the following two lines of code. After running, change the environment to python3 (the environment where the required packages are installed)

In [ ]:
from src.calculatechemopy import all_chemopy

In [ ]:
chemdf = all_chemopy('./molslibrary/allsmi.csv')
df.to_csv('./data/allsmi-chemopy.csv',index=0)

**3. Generate prediction dataset with 2 mutant amino acid descriptors**
- The chemopy descriptor files for all molecules generated have been obtained and are located in the '. /data' directory with the file name 'allsmi-chemopy.csv' 

In [ ]:
from src.moleculescreen import edatagenerator

In [ ]:
edatagenerator('./data/allsmi-chemopy.csv','./data/allsmi_3edata.csv')

**4. Predict with the BT model**

In [5]:
df_train = pd.read_csv('./model/train.csv')
features_columns = [col for col in df_train.columns if col not in ['label']]
df_allsmi_3e = pd.read_csv('./data/allsmi_3edata.csv',low_memory=False)
df_allsmi_3e.fillna(method='backfill',inplace=True)
X = df_allsmi_3e.loc[:, features_columns].values

In [6]:
# 加载 model
clf = jl.load('./model/bt-chemopy.pkl')
y_pred = clf.predict(X)
df_pred = pd.DataFrame(y_pred)
df_pred.value_counts()

D:\anaconda3\lib\site-packages\sklearn\base.py:329: UserWarning: Trying to unpickle estimator DecisionTreeClassifier from version 0.24.2 when using version 1.1.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
D:\anaconda3\lib\site-packages\sklearn\base.py:329: UserWarning: Trying to unpickle estimator BaggingClassifier from version 0.24.2 when using version 1.1.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(


0    3831
1     360
2      66
dtype: int64

**5. Draw the predicted small molecule structure**

- Small molecule naming format 'mutant - similar amino acid - predicted label value'

In [7]:
drawdata= pd.concat([df_allsmi_3e.loc[:,['SMILES','Name']],df_pred],axis=1)
drawdata.rename(columns={0:'label','SMILES':'smiles'},inplace=True)

L = round(drawdata.shape[0]/3)
drawdata.loc[0:L-1,'mutation']='IFRS'
drawdata.loc[L:L*2-1,'mutation']='MFRS'
drawdata.loc[L*2:L*3-1,'mutation']='BtaRS'

#去除预测结果中跟训练集重复的小分子smiles 格式
df95 = pd.read_csv('./model/train.smi',sep='\t')
drawdata = drawdata.drop(drawdata[drawdata.smiles.isin(df95.smiles)].index)

draw_1 = drawdata[drawdata.iloc[:,2]==1 ]
draw_2 = drawdata[drawdata.iloc[:,2]==2 ]
draw_p = pd.concat([draw_1,draw_2],axis=0)

print('The number of label=1:',draw_1.shape[0])
print('The number of label=2:',draw_2.shape[0])
print('The number of label>0:',draw_p.shape[0])

The number of label=1: 344
The number of label=2: 51
The number of label>0: 395


In [9]:
drawdf =draw_p
names=[]
drawsmi= drawdf['smiles'].values
database=[]
template = Chem.MolFromSmiles('CC(O)=O')  #template 作图法 让分子都根据一个基团显示
AllChem.Compute2DCoords(template)
for index,smi in enumerate(drawdf['smiles'].values):             
    mol=Chem.MolFromSmiles(smi)    # 转换SMILES 为rdkit分子对象
    AllChem.GenerateDepictionMatching2DStructure(mol,template) 
    names.append(drawdf['mutation'].values[index]+'-'+ drawdf['Name'].values[index].title() +'-'+str(drawdf['label'].values[index]))                      
    database.append(mol)
svg = Draw.MolsToGridImage(database,maxMols=999,molsPerRow=6,subImgSize=(250,350),legends=names,useSVG=True,returnPNG=True)
svg